hvPlot provides one API to explore data of many different types. Previous sections have exclusively worked with tabular data stored in pandas (or pandas-like) DataFrames. The other most common type of data are n-dimensional arrays. hvPlot aims to eventually support different array libraries but for now focuses on [xarray](http://xarray.pydata.org/en/stable/). XArray provides a convenient and very powerful wrapper to label the axis and coordinates of multi-dimensional (n-D) arrays. This user guide will cover how to leverage ``xarray`` and ``hvplot`` to visualize and explore data of different dimensionality ranging from simple 1D data, to 2D image-like data, to multi-dimensional cubes of data.

For these examples we’ll use the North American air temperature dataset:

In [1]:
import numpy as np
import xarray as xr
import hvplot.xarray

air_ds = xr.tutorial.open_dataset('air_temperature').load()
air = air_ds.air
air_ds

<xarray.Dataset>
Dimensions:  (lat: 25, lon: 53, time: 2920)
Coordinates:
  * lat      (lat) float32 75.0 72.5 70.0 67.5 65.0 ... 25.0 22.5 20.0 17.5 15.0
  * lon      (lon) float32 200.0 202.5 205.0 207.5 ... 322.5 325.0 327.5 330.0
  * time     (time) datetime64[ns] 2013-01-01 ... 2014-12-31T18:00:00
Data variables:
    air      (time, lat, lon) float32 241.2 242.5 243.5 ... 296.49 296.19 295.69
Attributes:
    Conventions:  COARDS
    title:        4x daily NMC reanalysis (1948)
    description:  Data is from NMC initialized reanalysis\n(4x/day).  These a...
    platform:     Model
    references:   http://www.esrl.noaa.gov/psd/data/gridded/data.ncep.reanaly...

## 1D Plots

Selecting the data at a particular lat/lon coordinate we get a 1D dataset of air temperatures over time:

In [2]:
air1d = air.isel(lat=10, lon=10)
air1d.hvplot()

:Curve   [time]   (air)

Notice how the axes are already appropriately labeled, because XArray stores the metadata required. We can also further subselect the data and use `*` to overlay plots:

In [3]:
air1d_sel = air1d.isel(time=slice(0, 200))
air1d_sel.hvplot(color='purple') * air1d_sel.hvplot.scatter(marker='o', color='blue', size=15)

:Overlay
   .Curve.I   :Curve   [time]   (air)
   .Scatter.I :Scatter   [time]   (air)

### Selecting multiple

If we select multiple coordinates along one axis and plot a chart type, the data will automatically be split by the coordinate:

In [27]:
air.isel(lon=10, lat=[19, 21, 22]).hvplot.line()

:NdOverlay   [lat]
   :Curve   [time]   (air)

In [28]:
help(air.isel(lon=10, lat=[19, 21, 22]).hvplot.line)

Help on method line in module hvplot:

line(x=None, y=None, **kwds) method of hvplot.hvPlot instance
    hvplot.line(x=None, y=None, alpha=None, color=None, hover_alpha=None, hover_color=None, hover_line_alpha=None, hover_line_color=None, line_alpha=None, line_cap=None, line_color=None, line_dash=None, line_join=None, line_width=None, muted_alpha=None, muted_color=None, muted_line_alpha=None, muted_line_color=None, nonselection_alpha=None, nonselection_color=None, nonselection_line_alpha=None, nonselection_line_color=None, selection_alpha=None, selection_color=None, selection_line_alpha=None, selection_line_color=None, width=None, height=None, shared_axes=None, grid=None, legend=None, rot=None, xlim=None, ylim=None, xticks=None, yticks=None, colorbar=None, invert=None, title=None, logx=None, logy=None, loglog=None, xaxis=None, yaxis=None, xformatter=None, yformatter=None, xlabel=None, ylabel=None, padding=None, datashade=None, rasterize=None, x_sampling=None, y_sampling=None, aggregato

In [26]:
air.isel(lon=10, lat=[19, 21, 22]).hvplot.line(color=['blue','red','green'], alpha=[1.0, 0.3, 0.5])

:NdOverlay   [lat]
   :Curve   [time]   (air)

To plot a different relationship we can explicitly request to display the latitude along the y-axis and use the by keyword to color each longitude (or 'lon') differently (note that this differs from the ``hue`` keyword xarray uses):

In [5]:
air.isel(time=10, lon=[10, 11]).hvplot.line(y='lat', by='lon')

:NdOverlay   [lon]
   :Curve   [air]   (lat)

## 2D Plots

By default the ``DataArray.hvplot()`` method generates an image if the data is two-dimensional.

In [6]:
air2d = air.isel(time=500)
air2d.hvplot(width=400)

:Image   [lon,lat]   (air)

Alternatively we can also plot the same data using the ``contour`` and ``contourf`` methods, which provide a ``levels`` argument to control the number of iso-contours to draw:

In [7]:
air2d.hvplot.contour(width=400, levels=20) + air2d.hvplot.contourf(width=400, levels=8)

:Layout
   .Contours.I :Contours   [lon,lat]   (air)
   .Polygons.I :Polygons   [lon,lat]   (air)

## n-D Plots

However if the data has more than two dimensions it will default to a histogram without providing it further hints:

In [8]:
air.hvplot()

:NdOverlay   [Element]
   :Histogram   [air]   (air_count)

However we can tell it to apply a ``groupby`` along a particular dimension, allowing us to explore the data as images along that dimension with a slider:

In [9]:
air.hvplot(groupby='time', width=500)

:DynamicMap   [time]
   :Image   [lon,lat]   (air)

If we pick a different, lower dimensional plot type (such as a 'line') it will automatically apply a groupby over the remaining dimensions:

In [10]:
air.hvplot.line()

:DynamicMap   [lon,lat]
   :Curve   [time]   (air)

## Statistical plots

Statistical plots such as histograms, kernel-density estimates, or violin and box-whisker plots aggregate the data across one or more of the coordinate dimensions. For instance, plotting a KDE provides a summary of all the air temperature values but we can, once again, use the by keyword to view each selected latitude (or 'lat') separately:

In [11]:
air.sel(lat=[25, 50, 75], method='nearest').hvplot.kde('air', by='lat', alpha=0.5)

:NdOverlay   [lat]
   :Distribution   [air]   (Density)

Using the ``by`` keyword we can break down the distribution of the air temperature across one or more variables:

In [12]:
air.hvplot.violin('air', by='lat', violin_color='lat', cmap='Category20')

:Violin   [lat]   (air)

## Datashading

If you are plotting a large amount of data at once, you can consider using the hvPlot interface to [Datashader](http://datashader.org), which can be enabled simply by setting `datashade=True`.

Note that be declaring that the data should not be grouped by another coordinate variable, by setting `groupby=[]`, we can plot all the datapoints, showing us the spread of air temperatures in the dataset:

In [13]:
air.hvplot.scatter('time', groupby=[], datashade=True) *\
air.groupby('time').mean(['lat', 'lon']).hvplot.line('time', color='indianred')

:DynamicMap   []
   :Overlay
      .RGB.I   :RGB   [time,air]   (R,G,B,A)
      .Curve.I :Curve   [time]   (air)

Here we also overlaid a non-datashaded line plot of the average temperature at each time.  If you enable the appropriate hover tool, the overlaid data supports hovering and zooming even in a static export such as on a web server or in an email, while the raw-data plot has been aggregated spatially before it is sent to the browser, and thus it has only the fixed spatial binning available at that time.  If you have a live Python process, the raw data will be aggregated each time you pan or zoom, letting you see the entire dataset regardless of size.